In [1]:
# Free tier
# symlink_to_notebooks = True                          # Enables the creation of symlinks back to /notebooks/
# model_storage_dir = '/tmp/stable-diffusion/models'   # Where the models will be downloaded to.
# repo_storage_dir = '/notebooks'                      # Where the repository will be downloaded to.
# export_storage_dir = '/notebooks/exports'            # Where the generated images will be exported to.

# Paid Tier
symlink_to_notebooks = False
model_storage_dir = '/storage/models'
repo_storage_dir = '/notebooks'
export_storage_dir = '/notebooks/exports'


# Other optional settings
# You don't have to change these if you don't want to

activate_xformers = True                               # Enables the xformers optimizations using pre-built wheels.
                                                       # Setting to True will automatically set up your environment/machine for xformers. 

link_novelai_anime_vae = False                         # Enables the linking of animevae.pt to each of the NovelAI models.
                                                       # Set to True if you've downloaded both the NovelAI models and hypernetworks.

download_scripts = False                               # Download custom scripts? Only reason why you would leave it disabled is because it may
                                                       # take a while to complete.

activate_deepdanbooru = False                          # Enable and install DeepDanbooru -> https://github.com/KichangKim/DeepDanbooru

activate_medvram = True                                # Enable medvram option.
                                                       # These are model optimizations which will reduce VRAM usage at the expense of some speed.
                                                       # Set to False if you have a lot of VRAM.

disable_pickle_check = False                           # Disable the automatic check for unexpected data in model files.
                                                       # Leave this set to False unless you have a reason to disable the check.

gradio_port = False                                    # Launch Gradio on a specific port. Set to False to let Gradio choose a port.
                                                       # This disables online Gradio app mode and you will only be able to access it on your local network.

gradio_auth = False                                    # Enable gradio_auth and insecure-extension-access option.
                                                       # Set to "me:password" to enable.

search_paperspace_datasets = True                      # Enable searching for checkpoints in /datasets to link to the webui

ui_theme = None                                        # Set the WEB UI theme. Values can be None (default) or 'dark'.

insecure_extension_access = False                      # Force enable extensions without a password.
                                                       # If you don't set a password, anyone can install and run arbitrary code on your machine!
                                                       # Instead, use gradio_auth which will automatically enable extensions when set.


# ===================================================================================================
# Save variables to Jupiter's temp storage so we can access it even if the kernel restarts.
%store symlink_to_notebooks model_storage_dir repo_storage_dir export_storage_dir activate_xformers link_novelai_anime_vae download_scripts activate_deepdanbooru activate_medvram disable_pickle_check gradio_port gradio_auth search_paperspace_datasets ui_theme insecure_extension_access

<mark>If you see any errors please check your settings!</mark>

**Don't forget, there's a block in the Tools section at the bottom to update this notebook to [the latest version](https://github.com/Engineer-of-Stuff/stable-diffusion-paperspace/blob/main/StableDiffusionUI_Voldemort_paperspace.ipynb) on GitHub.**

## Clone the WebUI repository

In [2]:
import os
# You'll see this little code block at the beginning of every cell.
# It makes sure you have ran the first block that defines your settings.
try:
    %store -r symlink_to_notebooks model_storage_dir repo_storage_dir
    test = [symlink_to_notebooks, model_storage_dir, repo_storage_dir]
except NameError as e:
    print("There is an issue with your variables.")
    print("Please go back to the first block and make sure your settings are correct, then run the cell.")
    print('Error:', e)
    import sys
    sys.exit(1)

%cd /notebooks/

def delete_broken_symlinks(path):
    # make sure to pass this function a path without a trailing slash
    for file in os.listdir(path):
        if os.path.islink(f'{path}/{file}') and not os.path.exists(os.readlink(f'{path}/{file}')):
            print(f'Symlink broken, removing: {file}')
            os.unlink(f'{path}/{file}')

def update_repo_if_not_exists(path, repo_clone_url, pre=None):
    if pre is not None:
        pre()    
    if not os.path.exists(path):
        !git clone "{repo_clone_url}" "{path}"
    else:
        print(f'{repo_clone_url.split("/")[-1]} already downloaded, updating...')
        !cd "{path}" && git pull # no % so we don't interfere with the main process

def init_free():
    if (symlink_to_notebooks and repo_storage_dir != '/notebooks'):
        delete_broken_symlinks('/notebooks/') # remove broken symlinks since it might have been installed in a non-persistent directory
        if not os.path.exists(repo_storage_dir):
            !mkdir -p "{repo_storage_dir}"
            !ln -s "{repo_storage_dir}" /notebooks/
            !ls -la /notebooks/kohya-ss
update_repo_if_not_exists(f'{repo_storage_dir}/kohya-ss', 'https://github.com/bmaltais/kohya_ss', init_free)

## Install requirements and download repositories

In [3]:
try:
    %store -r symlink_to_notebooks model_storage_dir repo_storage_dir activate_xformers download_scripts activate_deepdanbooru
    test = [symlink_to_notebooks, model_storage_dir, repo_storage_dir, activate_xformers, download_scripts, activate_deepdanbooru]
except NameError as e:
    print("There is an issue with your variables.")
    print("Please go back to the first block and make sure your settings are correct, then run the cell.")
    print('Error:', e)
    import sys
    sys.exit(1)

%cd "{repo_storage_dir}/kohya-ss"

!pip install --upgrade pip

import subprocess
import os
import sys
import importlib.util
import shlex
import platform
import argparse
import json

python = sys.executable
index_url = os.environ.get('INDEX_URL', "")
requirements_file = os.environ.get('REQS_FILE', "requirements.txt")

def run(command, desc=None, errdesc=None, custom_env=None):
    if desc is not None:
        print(desc)

    result = subprocess.run(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE, shell=True, env=os.environ if custom_env is None else custom_env)

    if result.returncode != 0:

        message = f"""{errdesc or 'Error running command'}.
Command: {command}
Error code: {result.returncode}
stdout: {result.stdout.decode(encoding="utf8", errors="ignore") if len(result.stdout)>0 else '<empty>'}
stderr: {result.stderr.decode(encoding="utf8", errors="ignore") if len(result.stderr)>0 else '<empty>'}
"""
        raise RuntimeError(message)

    return result.stdout.decode(encoding="utf8", errors="ignore")


def check_run(command):
    result = subprocess.run(command, stdout=subprocess.PIPE, stderr=subprocess.PIPE, shell=True)
    return result.returncode == 0


def is_installed(package):
    try:
        spec = importlib.util.find_spec(package)
    except ModuleNotFoundError:
        return False

    return spec is not None


def repo_dir(name):
    return os.path.join(dir_repos, name)


def run_python(code, desc=None, errdesc=None):
    return run(f'"{python}" -c "{code}"', desc, errdesc)


def run_pip(args, desc=None):
    index_url_line = f' --index-url {index_url}' if index_url != '' else ''
    return run(f'"{python}" -m pip {args} --prefer-binary{index_url_line}', desc=f"Installing {desc}", errdesc=f"Couldn't install {desc}")


run_pip(f"install -r {requirements_file}", "requirements for Web UI")

if activate_xformers:
    print('Installing xformers...')
    import subprocess
    def download_release(url):
        binary = 'xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl' # have to save the binary as a specific name that pip likes
        tmp_dir = subprocess.check_output(['mktemp', '-d']).decode('ascii').strip('\n')
        !wget "{url}" -O "{tmp_dir}/{binary}"
        return os.path.join(tmp_dir, binary)

    # Set up pip packages
    !pip uninstall -y torch  torchvision torchaudio # Remove existing pytorch install.
    !pip install torch torchvision torchaudio --extra-index-url https://download.pytorch.org/whl/cu113 # Install pytorch for cuda 11.3
    s = subprocess.getoutput('nvidia-smi')
    if 'A4000' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/A4000-Oct-28-2022/a4000-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'A5000' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/A5000-Nov-1-2022/a5000-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'A6000' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/A6000-Nov-1-2022/a6000-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'P5000' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/P5000-Nov-1-2022/p5000-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'RTX 4000' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/RTX-4000-Nov-1-2022/rtx4000-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'RTX 5000' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/RTX-5000-Nov-1-2022/rtx5000-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'A100' in s:
        xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/A100-Nov-1-2022/a100-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    elif 'M4000' in s:
        print('xformers for M4000 hasn\'t been built yet.')
        # xformers_whl = download_release('https://github.com/Cyberes/xformers-compiled/releases/download/A100-Nov-1-2022/a100-xformers-0.0.14.dev0-cp39-cp39-linux_x86_64.whl')
    else:
        print('GPU not matched to xformers binary so a one-size-fits-all binary was installed. If you have any issues, please build xformers using the Tools block below.')
        xformers_whl = download_release('https://raw.githubusercontent.com/Cyberes/xformers-compiled/main/various/xformers-0.0.14.dev0-cp37-cp37m-linux_x86_64.whl')
    !pip install --force-reinstall "{xformers_whl}"

!echo -e "\n===================================\nDone! If you're seeing this the process has exited successfully.\n"

In [23]:
!mkdir -p ~/.cache/huggingface/accelerate
!echo -e "command_file: null\ncommands: null\ncompute_environment: LOCAL_MACHINE\ndeepspeed_config: {}\ndistributed_type: 'NO'\ndowncast_bf16: 'no'\ndynamo_backend: 'NO'\nfsdp_config: {}\ngpu_ids: all\nmachine_rank: 0\nmain_process_ip: null\nmain_process_port: null\nmain_training_function: main\nmegatron_lm_config: {}\nmixed_precision: fp16\nnum_machines: 1\nnum_processes: 1\nrdzv_backend: static\nsame_network: true\ntpu_name: null\ntpu_zone: null\nuse_cpu: false" > ~/.cache/huggingface/accelerate/default_config.yaml

In [24]:
%cd /notebooks/kohya-ss
!accelerate launch --num_cpu_threads_per_process 8 train_network.py \
--pretrained_model_name_or_path=/storage/models/nai.ckpt \
--train_data_dir=/storage/data \
--output_dir=/notebooks/sd-output \
--prior_loss_weight=1.0 \
--resolution=512 \
--train_batch_size=1 \
--learning_rate=9e-5 \
--max_train_steps=10000 \
--use_8bit_adam \
--xformers \
--mixed_precision="fp16" \
--save_every_n_epochs=300 \
--save_model_as=safetensors \
--clip_skip=2 \
--seed=41 \
--color_aug \
--network_module=networks.lora 